In [1]:
import json
import os
import time
import random
from PIL import Image
import numpy as np
import matplotlib.pyplot as plt
from tqdm import tqdm
import shutil

import torch
import torch.nn as nn
import torch.backends.cudnn as cudnn
import torch.optim as optim
from torch.utils.data import DataLoader
from torchvision import datasets
from torchvision import transforms
from torchvision import models
from torchsummary import summary
from sklearn.model_selection import train_test_split

from model_pytorch import EfficientNet
from utils import Bar,Logger, AverageMeter, accuracy, mkdir_p, savefig
from warmup_scheduler import GradualWarmupScheduler

from PIL import ImageFile
ImageFile.LOAD_TRUNCATED_IMAGES = True
import collections

In [2]:
# GPU Device
gpu_id = 0
os.environ['CUDA_VISIBLE_DEVICES'] = str(gpu_id)
use_cuda = torch.cuda.is_available()
print("GPU device %d:" %(gpu_id), use_cuda)

GPU device 0: True


# Arguments

In [3]:
source_dir = '/media/data2/dataset/GAN_ImageData/PGGAN_128/'
target_dir = '/media/data2/dataset/GAN_ImageData/StyleGAN_256/'

In [4]:
pretrained = './log/pggan/128/b1/checkpoint.pth.tar'
resume = ''

In [5]:
# Model
model_name = 'efficientnet-b1' # b0-b7 scale

# Optimization
num_classes = 2
epochs = 7000
start_epoch = 0
train_batch = 12
test_batch = 200
lr = 0.04
schedule = [1500, 3000, 4500, 6000]
momentum = 0
gamma = 0.1 # LR is multiplied by gamma on schedule

# CheckPoint
checkpoint = './log/pggan/128/b1/to_style1/cutmix' # dir
if not os.path.isdir(checkpoint):
    os.makedirs(checkpoint)
num_workers = 4

# Seed
manual_seed = 7
random.seed(manual_seed)
torch.cuda.manual_seed_all(manual_seed)

# Image
size = (128, 128)

# sp
sp_alpha = 0.1
sp_beta = 0.1
fc_name = 'fc.'

# iterative training
feedback = 0
iter_time = [1000, 2000, 2500]

# cutmix
cm_prob = 0.5
cm_prob_init = 0.99
cm_prob_low = 0.1

best_acc = 0

In [6]:
state = {}
state['num_classes'] = num_classes
state['epochs'] = epochs
state['start_epoch'] = start_epoch
state['train_batch'] = train_batch
state['test_batch'] = test_batch
state['lr'] = lr
state['schedule'] = schedule
state['momentum'] = momentum
state['gamma'] = gamma

# Dataset

In [7]:
train_dir = os.path.join(target_dir, '100_shot')
source_train_dir = os.path.join(target_dir, '100_shot_pggan_only')
val_target_dir = os.path.join(target_dir, 'validation')
val_source_dir = os.path.join(source_dir, 'validation')

train_aug = transforms.Compose([
    transforms.RandomAffine(degrees=2, translate=(0.02, 0.02), scale=(0.98, 1.02), shear=2, fillcolor=(124,117,104)),
    transforms.Resize(size),
    transforms.RandomHorizontalFlip(),
    transforms.ToTensor(),
#     transforms.RandomErasing(p=0.3, scale=(0.02, 0.10), ratio=(0.3, 3.3), value=0, inplace=True),
])
val_aug = transforms.Compose([
    transforms.Resize(size),
    transforms.ToTensor(),
])

# pin_memory : cuda pin memeory use
train_loader = DataLoader(datasets.ImageFolder(train_dir, transform=train_aug),
                          batch_size=train_batch, shuffle=True, num_workers=num_workers, pin_memory=True)
source_train_loader = DataLoader(datasets.ImageFolder(source_train_dir, transform=val_aug),
                                batch_size=train_batch, shuffle=True, num_workers=num_workers, pin_memory=True)
val_target_loader = DataLoader(datasets.ImageFolder(val_target_dir, val_aug),
                       batch_size=test_batch, shuffle=True, num_workers=num_workers, pin_memory=True)
val_source_loader = DataLoader(datasets.ImageFolder(val_source_dir, val_aug),
                       batch_size=test_batch, shuffle=True, num_workers=num_workers, pin_memory=True)

# Model

In [8]:
teacher_model = EfficientNet.from_name(model_name, num_classes=num_classes)
student_model = EfficientNet.from_name(model_name, num_classes=num_classes, 
                                       override_params={'dropout_rate':0.5})

# Pre-trained
if pretrained:
    print("=> using pre-trained model '{}'".format(pretrained))
    teacher_model.load_state_dict(torch.load(pretrained)['state_dict'])
    student_model.load_state_dict(torch.load(pretrained)['state_dict'])

=> using pre-trained model './log/pggan/128/b1/checkpoint.pth.tar'


In [9]:
teacher_model.to('cuda')
student_model.to('cuda')
cudnn.benchmark = True
print('    Total params: %.2fM' % (sum(p.numel() for p in student_model.parameters())/1000000.0))

    Total params: 6.52M


In [10]:
for param in teacher_model.parameters():
    param.requires_grad = False
teacher_model.eval()

EfficientNet(
  (_conv_stem): Conv2dStaticSamePadding(
    3, 32, kernel_size=(3, 3), stride=(2, 2), bias=False
    (static_padding): ZeroPad2d(padding=(0, 1, 0, 1), value=0.0)
  )
  (_bn0): GroupNorm(8, 32, eps=1e-05, affine=True)
  (_blocks): ModuleList(
    (0): MBConvBlock(
      (_depthwise_conv): Conv2dStaticSamePadding(
        32, 32, kernel_size=(3, 3), stride=[1, 1], groups=32, bias=False
        (static_padding): ZeroPad2d(padding=(1, 1, 1, 1), value=0.0)
      )
      (_bn1): GroupNorm(8, 32, eps=1e-05, affine=True)
      (_se_reduce): Conv2dStaticSamePadding(
        32, 8, kernel_size=(1, 1), stride=(1, 1)
        (static_padding): Identity()
      )
      (_se_expand): Conv2dStaticSamePadding(
        8, 32, kernel_size=(1, 1), stride=(1, 1)
        (static_padding): Identity()
      )
      (_project_conv): Conv2dStaticSamePadding(
        32, 16, kernel_size=(1, 1), stride=(1, 1), bias=False
        (static_padding): Identity()
      )
      (_bn2): GroupNorm(4, 16, ep

In [11]:
teacher_model_weights = {}
for name, param in teacher_model.named_parameters():
    teacher_model_weights[name] = param.detach()

In [12]:
def rand_bbox(size, lam):
    W = size[2]
    H = size[3]
    cut_rat = np.sqrt(1. - lam)
    cut_w = np.int(W * cut_rat)
    cut_h = np.int(H * cut_rat)

    # uniform
    cx = np.random.randint(W)
    cy = np.random.randint(H)

    bbx1 = np.clip(cx - cut_w // 2, 0, W)
    bby1 = np.clip(cy - cut_h // 2, 0, H)
    bbx2 = np.clip(cx + cut_w // 2, 0, W)
    bby2 = np.clip(cy + cut_h // 2, 0, H)

    return bbx1, bby1, bbx2, bby2

In [13]:
def reg_cls(model):
    l2_cls = torch.tensor(0.).cuda()
    for name, param in model.named_parameters():
        if name.startswith(fc_name):
            l2_cls += 0.5 * torch.norm(param) ** 2
    return l2_cls

def reg_l2sp(model):
    sp_loss = torch.tensor(0.).cuda()
    for name, param in model.named_parameters():
        if not name.startswith(fc_name):
            sp_loss += 0.5 * torch.norm(param - teacher_model_weights[name]) ** 2
    return sp_loss

# Loss

In [14]:
criterion = nn.CrossEntropyLoss().cuda()
optimizer = optim.SGD(student_model.parameters(), lr=lr, momentum=momentum)
# optimizer = optim.Adam(model.parameters(), weight_decay=0)
scheduler_cosine = torch.optim.lr_scheduler.CosineAnnealingLR(optimizer, epochs)
scheduler_warmup = GradualWarmupScheduler(optimizer, multiplier=8, total_epoch=10, after_scheduler=scheduler_cosine)

In [15]:
# Resume
if resume:
    print('==> Resuming from checkpoint..')
    checkpoint = os.path.dirname(resume)
#     checkpoint = torch.load(resume)
    resume = torch.load(resume)
    best_acc = resume['best_acc']
    start_epoch = resume['epoch']
    student_model.load_state_dict(resume['state_dict'])
    optimizer.load_state_dict(resume['optimizer'])
    logger = Logger(os.path.join(checkpoint, 'log.txt'), resume=True)
else:
    logger = Logger(os.path.join(checkpoint, 'log.txt'))
    logger.set_names(['Learning Rate', 'Train Loss', 'Valid Loss', 'Train Acc.', 'Valid Acc.', 'Source Loss', 'Source ACC.'])

# Train

In [16]:
def train(train_loader, source_train_loader, teacher_model, student_model, criterion, optimizer, epoch, use_cuda):
    student_model.train()
    torch.set_grad_enabled(True)
    
    batch_time = AverageMeter()
    data_time = AverageMeter()
    losses = AverageMeter()
    top1 = AverageMeter()
    end = time.time()
    
    source_set = []
    for inputs, targets in source_train_loader:
        source_set.append((inputs, targets))
    
    bar = Bar('Processing', max=len(train_loader))
    for batch_idx, (inputs, targets) in enumerate(train_loader):
        batch_size = inputs.size(0)
        if batch_size < train_batch:
            continue
        # measure data loading time
        data_time.update(time.time() - end)

        if use_cuda:
            inputs, targets = inputs.cuda(), targets.cuda()
        inputs, targets = torch.autograd.Variable(inputs), torch.autograd.Variable(targets)
        
        # cutmix
        r = np.random.rand(1)
        if r < cm_prob:
            source_inputs, source_targets = source_set[batch_idx]
            source_inputs, source_targets = source_inputs.cuda(), source_targets.cuda()
            
            prob_delta = cm_prob_init - cm_prob_low
            prob_step = epoch / (epochs+1) * prob_delta
            lam = cm_prob_init - prob_step
            
            rand_index = torch.randperm(inputs.size()[0]).cuda()
            
            bbx1, bby1, bbx2, bby2 = rand_bbox(inputs.size(), lam)
            inputs[rand_index, :, bbx1:bbx2, bby1:bby2] = source_inputs[rand_index, :, bbx1:bbx2, bby1:bby2]
            # teacher model output, prediction
            
            teacher_outputs = nn.Softmax()(teacher_model(inputs))
            pred = teacher_outputs.argmax(dim=-1)
            lam = 1 - ((bbx2 - bbx1)*(bby2 - bby1) / (inputs.size()[-1] * inputs.size()[-2]))
            target_a = pred
            target_b = pred[rand_index]
            
            outputs = student_model(inputs)
            loss_main = criterion(outputs, target_a) * lam + criterion(outputs, target_b) * (1. - lam)
            loss_cls = 0
            loss_sp = 0
            loss_cls = reg_cls(student_model)
            loss_sp = reg_l2sp(student_model)
            
        else:
            source_inputs, source_targets = source_set[batch_idx]
            source_inputs, source_targets = source_inputs.cuda(), source_targets.cuda()
            
            prob_delta = cm_prob_init - cm_prob_low
            prob_step = epoch / (epochs+1) * prob_delta
            lam = cm_prob_init - prob_step
            
            rand_index = torch.randperm(inputs.size()[0]).cuda()
            
            bbx1, bby1, bbx2, bby2 = rand_bbox(inputs.size(), lam)
            inputs[rand_index, :, bbx1:bbx2, bby1:bby2] = source_inputs[rand_index, :, bbx1:bbx2, bby1:bby2]
            # teacher model output, prediction
            
            lam = 1 - ((bbx2 - bbx1)*(bby2 - bby1) / (inputs.size()[-1] * inputs.size()[-2]))
            
            target_a = targets
            target_b = targets[rand_index]
            
            outputs = student_model(inputs)
            loss_main = criterion(outputs, target_a) * lam + criterion(outputs, target_b) * (1. - lam)
            loss_cls = 0
            loss_sp = 0
            loss_cls = reg_cls(student_model)
            loss_sp = reg_l2sp(student_model)
            
        # compute output
        loss = loss_main + sp_alpha*loss_sp + sp_beta*loss_cls

        # measure accuracy and record loss
        prec1 = accuracy(outputs.data, targets.data)
        losses.update(loss.data.tolist(), inputs.size(0))
        top1.update(prec1[0], inputs.size(0))

        # compute gradient and do SGD step
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        # measure elapsed time
        batch_time.update(time.time() - end)
        end = time.time()

        # plot progress
        bar.suffix  = '({batch}/{size}) Data: {data:.3f}s | Batch: {bt:.3f}s | Total: {total:} | ETA: {eta:} | Loss: {loss:.4f} | top1: {top1: .4f} '.format(
                    batch=batch_idx + 1,
                    size=len(train_loader),
                    data=data_time.val,
                    bt=batch_time.val,
                    total=bar.elapsed_td,
                    eta=bar.eta_td,
                    loss=losses.avg,
                    top1=top1.avg,
                    )
        bar.next()
#         if batch_idx % 10 == 0:
        print('{batch}/{size} Data:{data:.3f} | Batch:{bt:.3f} | Total:{total:} | ETA:{eta:} | Loss:{loss:} | top1:{tp1:}'.format(
                 batch=batch_idx+1, size=len(train_loader), data=data_time.val, bt=batch_time.val, total=bar.elapsed_td, eta=bar.eta_td, loss=losses.avg, tp1=top1.avg))
    bar.finish()
    return (losses.avg, top1.avg)

In [17]:
def test(val_loader, model, criterion, epoch, use_cuda):
    global best_acc

    batch_time = AverageMeter()
    data_time = AverageMeter()
    losses = AverageMeter()
    top1 = AverageMeter()

    # switch to evaluate mode
    model.eval()
    torch.set_grad_enabled(False)

    end = time.time()
    bar = Bar('Processing', max=len(val_loader))
    for batch_idx, (inputs, targets) in enumerate(val_loader):
        # measure data loading time
        data_time.update(time.time() - end)

        if use_cuda:
            inputs, targets = inputs.cuda(), targets.cuda()
        inputs, targets = torch.autograd.Variable(inputs, volatile=True), torch.autograd.Variable(targets)

        # compute output
        outputs = model(inputs)
        loss_main = criterion(outputs, targets)
        loss_cls = 0
        loss_sp = 0
        loss_cls = reg_cls(model)
        loss_sp = reg_l2sp(model)
        loss = loss_main + sp_alpha*loss_sp + sp_beta*loss_cls

        # measure accuracy and record loss
        prec1 = accuracy(outputs.data, targets.data)
        losses.update(loss.data.tolist(), inputs.size(0))
        top1.update(prec1[0], inputs.size(0))

        # measure elapsed time
        batch_time.update(time.time() - end)
        end = time.time()

        # plot progress
        bar.suffix  = '({batch}/{size}) Data: {data:.3f}s | Batch: {bt:.3f}s | Total: {total:} | ETA: {eta:} | Loss: {loss:} | top1: {top1:}'.format(
                    batch=batch_idx + 1,
                    size=len(val_loader),
                    data=data_time.avg,
                    bt=batch_time.avg,
                    total=bar.elapsed_td,
                    eta=bar.eta_td,
                    loss=losses.avg,
                    top1=top1.avg,)
        bar.next()
    print('{batch}/{size} Data:{data:.3f} | Batch:{bt:.3f} | Total:{total:} | ETA:{eta:} | Loss:{loss:} | top1:{tp1:}'.format(
         batch=batch_idx+1, size=len(val_loader), data=data_time.val, bt=batch_time.val, total=bar.elapsed_td, eta=bar.eta_td, loss=losses.avg, tp1=top1.avg))
    bar.finish()
    return (losses.avg, top1.avg)

In [18]:
def save_checkpoint(state, is_best, checkpoint='checkpoint', filename='checkpoint.pth.tar'):
    filepath = os.path.join(checkpoint, filename)
    torch.save(state, filepath)
    if is_best:
        shutil.copyfile(filepath, os.path.join(checkpoint, 'model_best.pth.tar'))

def adjust_learning_rate(optimizer, epoch):
    global state
    lr_set = [1, 1e-1, 1e-2, 1e-3, 1e-4, 1e-5]
    lr_list = schedule.copy()
    lr_list.append(epoch)
    lr_list.sort()
    idx = lr_list.index(epoch)
    state['lr'] *= lr_set[idx]
    for param_group in optimizer.param_groups:
        param_group['lr'] = state['lr']

In [ ]:
for epoch in range(start_epoch, epochs):
    # teacher feedback
    if epoch in iter_time:
        print("iterative training: feedback {}".format(epoch))
        teacher_model.load_state_dict(student_model.state_dict())
        teacher_model_weights = {}
        for name, param in teacher_model.named_parameters():
            teacher_model_weights[name] = param.detach()
    
    state['lr'] = optimizer.state_dict()['param_groups'][0]['lr']
    adjust_learning_rate(optimizer, epoch)
    print('\nEpoch: [%d | %d] LR: %f' % (epoch + 1, epochs, state['lr']))
    
    train_loss, train_acc = train(source_train_loader, train_loader, teacher_model, student_model, criterion, optimizer, epoch, use_cuda)
    
    if epoch % 20 == 0:
        test_loss, test_acc = test(val_target_loader, student_model, criterion, epoch, use_cuda)
        source_loss, source_acc = test(val_source_loader, student_model, criterion, epoch, use_cuda)

    
        logger.append([state['lr'], train_loss, test_loss, train_acc, test_acc, source_loss, source_acc])
        is_best = test_acc > best_acc
        best_acc = max(test_acc, best_acc)
        save_checkpoint({
            'epoch': epoch + 1,
            'state_dict' : student_model.state_dict(),
            'acc': test_acc,
            'best_acc': best_acc,
            'optimizer': optimizer.state_dict(),
        }, is_best, checkpoint=checkpoint)
    scheduler_warmup.step()


Epoch: [1 | 7000] LR: 0.040000
1/17 Data:0.850 | Batch:3.889 | Total:0:00:03 | ETA:0:00:53 | Loss:0.05466274917125702 | top1:100.0


/home/cutz/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:43: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.


2/17 Data:0.001 | Batch:0.308 | Total:0:00:03 | ETA:0:00:28 | Loss:0.04396321065723896 | top1:100.0
3/17 Data:0.002 | Batch:0.292 | Total:0:00:03 | ETA:0:00:19 | Loss:0.07816479727625847 | top1:97.22222137451172
4/17 Data:0.000 | Batch:0.293 | Total:0:00:04 | ETA:0:00:14 | Loss:0.5293257394805551 | top1:91.66667175292969
5/17 Data:0.001 | Batch:0.241 | Total:0:00:04 | ETA:0:00:11 | Loss:0.43863464072346686 | top1:93.33333587646484
6/17 Data:0.001 | Batch:0.298 | Total:0:00:04 | ETA:0:00:09 | Loss:0.6338578717162212 | top1:90.27777862548828
7/17 Data:0.003 | Batch:0.233 | Total:0:00:04 | ETA:0:00:08 | Loss:1.3282994420400687 | top1:83.33333587646484
8/17 Data:0.001 | Batch:0.302 | Total:0:00:05 | ETA:0:00:06 | Loss:1.3057702970691025 | top1:76.04167175292969
9/17 Data:0.001 | Batch:0.234 | Total:0:00:05 | ETA:0:00:05 | Loss:1.2410677841140165 | top1:75.0
10/17 Data:0.001 | Batch:0.266 | Total:0:00:05 | ETA:0:00:05 | Loss:1.1528263602405786 | top1:75.83333587646484
11/17 Data:0.001 | Bat

/home/cutz/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:21: UserWarning: volatile was removed and now has no effect. Use `with torch.no_grad():` instead.


39/39 Data:0.002 | Batch:0.264 | Total:0:00:13 | ETA:0:00:00 | Loss:0.791289413586641 | top1:50.102561950683594
161/161 Data:0.002 | Batch:1.032 | Total:0:00:44 | ETA:0:00:00 | Loss:0.39122152625586015 | top1:80.98754119873047

Epoch: [2 | 7000] LR: 0.068000
1/17 Data:0.911 | Batch:1.191 | Total:0:00:00 | ETA:0:00:10 | Loss:0.5510168075561523 | top1:66.66667175292969
2/17 Data:0.002 | Batch:0.285 | Total:0:00:00 | ETA:0:00:07 | Loss:0.5051204711198807 | top1:75.0
3/17 Data:0.001 | Batch:0.222 | Total:0:00:01 | ETA:0:00:06 | Loss:0.4747142195701599 | top1:75.0
4/17 Data:0.001 | Batch:0.267 | Total:0:00:01 | ETA:0:00:05 | Loss:0.4513489902019501 | top1:77.08333587646484
5/17 Data:0.002 | Batch:0.261 | Total:0:00:01 | ETA:0:00:04 | Loss:0.4177935361862183 | top1:80.00000762939453
6/17 Data:0.002 | Batch:0.213 | Total:0:00:01 | ETA:0:00:04 | Loss:0.3976456622282664 | top1:81.94444274902344
7/17 Data:0.002 | Batch:0.210 | Total:0:00:02 | ETA:0:00:03 | Loss:0.4159769671303885 | top1:80.95238

...

1/17 Data:1.271 | Batch:1.703 | Total:0:00:00 | ETA:0:00:14 | Loss:0.41906097531318665 | top1:75.0
2/17 Data:0.001 | Batch:0.314 | Total:0:00:01 | ETA:0:00:09 | Loss:0.4461597055196762 | top1:79.16667175292969
3/17 Data:0.002 | Batch:0.316 | Total:0:00:01 | ETA:0:00:07 | Loss:0.5060836970806122 | top1:77.77777862548828
4/17 Data:0.002 | Batch:0.306 | Total:0:00:01 | ETA:0:00:06 | Loss:0.4907829165458679 | top1:81.25
5/17 Data:0.003 | Batch:0.352 | Total:0:00:02 | ETA:0:00:06 | Loss:0.46930053234100344 | top1:81.66667175292969
6/17 Data:0.002 | Batch:0.412 | Total:0:00:02 | ETA:0:00:05 | Loss:0.48148196935653687 | top1:81.94444274902344
7/17 Data:0.003 | Batch:0.352 | Total:0:00:02 | ETA:0:00:05 | Loss:0.5180794596672058 | top1:79.76190948486328
8/17 Data:0.002 | Batch:0.331 | Total:0:00:03 | ETA:0:00:04 | Loss:0.5285411477088928 | top1:79.16667175292969
9/17 Data:0.002 | Batch:0.354 | Total:0:00:03 | ETA:0:00:04 | Loss:0.5131620433595445 | top1:81.48148345947266
10/17 Data:0.001 | Batc

11/17 Data:0.001 | Batch:5.749 | Total:0:00:48 | ETA:0:00:26 | Loss:0.45298971371217206 | top1:78.78787994384766
12/17 Data:0.001 | Batch:3.385 | Total:0:00:51 | ETA:0:00:22 | Loss:0.4419909069935481 | top1:80.55555725097656
13/17 Data:0.001 | Batch:4.442 | Total:0:00:55 | ETA:0:00:17 | Loss:0.4405638254605807 | top1:78.84615325927734
14/17 Data:0.002 | Batch:4.020 | Total:0:00:59 | ETA:0:00:13 | Loss:0.43204954266548157 | top1:79.76190948486328
15/17 Data:0.001 | Batch:4.759 | Total:0:01:04 | ETA:0:00:09 | Loss:0.4294312516848246 | top1:80.55555725097656
16/17 Data:0.003 | Batch:3.919 | Total:0:01:08 | ETA:0:00:05 | Loss:0.43722423166036606 | top1:80.20833587646484

Epoch: [2230 | 7000] LR: 0.024706
1/17 Data:14.006 | Batch:14.406 | Total:0:00:03 | ETA:0:00:55 | Loss:0.46705561876296997 | top1:66.66667175292969
2/17 Data:0.003 | Batch:1.170 | Total:0:00:04 | ETA:0:00:35 | Loss:0.3866996765136719 | top1:66.66667175292969
3/17 Data:0.032 | Batch:3.552 | Total:0:00:08 | ETA:0:00:38 | Los

4/17 Data:0.001 | Batch:3.184 | Total:0:00:17 | ETA:0:00:58 | Loss:0.542101077735424 | top1:81.25
5/17 Data:0.000 | Batch:3.168 | Total:0:00:20 | ETA:0:00:50 | Loss:0.5104360938072204 | top1:85.00000762939453
6/17 Data:0.001 | Batch:3.583 | Total:0:00:24 | ETA:0:00:45 | Loss:0.49907977879047394 | top1:87.5
7/17 Data:0.001 | Batch:3.057 | Total:0:00:27 | ETA:0:00:40 | Loss:0.5206996585641589 | top1:84.52381134033203
8/17 Data:0.001 | Batch:3.686 | Total:0:00:31 | ETA:0:00:35 | Loss:0.5293566770851612 | top1:83.33333587646484
9/17 Data:0.003 | Batch:4.409 | Total:0:00:35 | ETA:0:00:32 | Loss:0.5428699751694998 | top1:82.40740966796875
10/17 Data:0.001 | Batch:5.977 | Total:0:00:41 | ETA:0:00:30 | Loss:0.5396732896566391 | top1:81.66667175292969
11/17 Data:0.001 | Batch:5.626 | Total:0:00:47 | ETA:0:00:24 | Loss:0.5239992493932898 | top1:83.33333587646484
12/17 Data:0.001 | Batch:3.764 | Total:0:00:50 | ETA:0:00:21 | Loss:0.5172078212102255 | top1:83.33333587646484
13/17 Data:0.001 | Batc

14/17 Data:0.002 | Batch:0.333 | Total:0:00:04 | ETA:0:00:01 | Loss:0.445955502135413 | top1:80.35714721679688
15/17 Data:0.002 | Batch:0.301 | Total:0:00:04 | ETA:0:00:01 | Loss:0.43856306274731954 | top1:80.0
16/17 Data:0.003 | Batch:0.245 | Total:0:00:05 | ETA:0:00:01 | Loss:0.46132602356374264 | top1:78.64583587646484

Epoch: [2239 | 7000] LR: 0.024652
1/17 Data:1.149 | Batch:1.507 | Total:0:00:00 | ETA:0:00:13 | Loss:0.4756025969982147 | top1:66.66667175292969
2/17 Data:0.003 | Batch:3.773 | Total:0:00:04 | ETA:0:00:34 | Loss:0.4591038227081299 | top1:66.66667175292969
3/17 Data:0.001 | Batch:4.922 | Total:0:00:09 | ETA:0:00:45 | Loss:0.44858504335085553 | top1:75.0
4/17 Data:0.001 | Batch:3.113 | Total:0:00:12 | ETA:0:00:41 | Loss:0.382269237190485 | top1:70.83333587646484
5/17 Data:0.001 | Batch:4.151 | Total:0:00:16 | ETA:0:00:41 | Loss:0.3452085733413696 | top1:68.33333587646484
6/17 Data:0.001 | Batch:2.465 | Total:0:00:19 | ETA:0:00:36 | Loss:0.38350746035575867 | top1:70.83

6/17 Data:0.001 | Batch:4.382 | Total:0:00:32 | ETA:0:01:01 | Loss:0.43467120826244354 | top1:72.22222137451172
7/17 Data:0.001 | Batch:1.225 | Total:0:00:33 | ETA:0:00:49 | Loss:0.42144510575703215 | top1:76.19047546386719
8/17 Data:0.001 | Batch:1.307 | Total:0:00:35 | ETA:0:00:40 | Loss:0.4661073610186577 | top1:78.125
9/17 Data:0.002 | Batch:5.479 | Total:0:00:40 | ETA:0:00:37 | Loss:0.452072497871187 | top1:75.9259262084961
10/17 Data:0.003 | Batch:5.549 | Total:0:00:46 | ETA:0:00:33 | Loss:0.44523346424102783 | top1:76.66667175292969
11/17 Data:0.001 | Batch:4.012 | Total:0:00:50 | ETA:0:00:26 | Loss:0.4451984465122223 | top1:77.2727279663086
12/17 Data:0.001 | Batch:5.394 | Total:0:00:55 | ETA:0:00:22 | Loss:0.4444431985418002 | top1:77.77777862548828
13/17 Data:0.001 | Batch:3.801 | Total:0:00:59 | ETA:0:00:18 | Loss:0.46120831828850967 | top1:77.56410217285156
14/17 Data:0.001 | Batch:5.163 | Total:0:01:04 | ETA:0:00:13 | Loss:0.4536266305616924 | top1:77.38095092773438
15/17 